In [272]:
import os
import ee
import geemap

In [ ]:
ee.Authenticate()
ee.Initialize()

In [274]:
Map = geemap.Map()
Map.add_basemap("HYBRID")
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [275]:
area_int = Map.user_roi
area_int.getInfo()

{'type': 'Polygon',
 'coordinates': [[[-42.011719, -8.581021],
   [-37.177734, -8.581021],
   [-37.177734, -1.845384],
   [-42.011719, -1.845384],
   [-42.011719, -8.581021]]]}

In [276]:
def melhores_imagens(ano):
    ano_inicio = ee.Date.fromYMD(ano, 1, 1)
    ano_fim = ano_inicio.advance(1, 'year')

    image = ee.ImageCollection('MODIS/061/MCD43A4')\
          .filterDate(ano_inicio, ano_fim)\
          .filterBounds(area_int)\
          .sort("CLOUD_COVER")\
          .first()
    return image

In [277]:
anos = ee.List.sequence(2002, 2022)

In [278]:
imagens = anos.map(melhores_imagens)

In [279]:
contar = imagens.size().getInfo()
print(contar)

21


In [280]:
lista_anos = anos.getInfo()
lista_anos

[2002,
 2003,
 2004,
 2005,
 2006,
 2007,
 2008,
 2009,
 2010,
 2011,
 2012,
 2013,
 2014,
 2015,
 2016,
 2017,
 2018,
 2019,
 2020,
 2021,
 2022]

In [288]:
props = {
    'bands': [
  'Nadir_Reflectance_Band1', 'Nadir_Reflectance_Band4',
  'Nadir_Reflectance_Band3'
],
    'min': 0.0,
    'max': 1000,
    'gamma': 0.5,
}

In [282]:
for index in range(0, contar):
    imagem = ee.Image(imagens.get(index))
    nome_camada = "Imagem " + str(lista_anos[index])
    Map.addLayer(imagem, props, nome_camada, False)

In [ ]:
Map

## GIF CONFIGURAÇÕES

In [284]:
saida_gif = os.path.join("./", "mapa-ce-teste3.gif")

In [285]:
video_args = {
    'dimensions': 768,
    'region': area_int,
    'framesPerSecond': 4,
    'bands': [
    'Nadir_Reflectance_Band1', 'Nadir_Reflectance_Band4',
    'Nadir_Reflectance_Band3'
    ],
    'min': 0.0,
    'max': 4000.0,
    'gamma': 1.4,
}

In [286]:
texto_gif = os.path.join("./", "mapa-ce-teste3.gif")
geemap.add_text_to_gif(saida_gif, texto_gif, xy=('3%', '5%'), text_sequence=2002, font_size=30, font_color='#ffffff', duration=200)

The input gif file does not exist.


In [287]:
geemap.download_ee_video(ee.ImageCollection(imagens), video_args, saida_gif)

Generating URL...
Please wait ...
The GIF image has been saved to: /content/mapa-ce-teste3.gif


In [ ]:
geemap.show_image(saida_gif)